In [1]:
import os
import glob
import json
from datetime import datetime, timezone
from sklearn.preprocessing import MinMaxScaler
import pandas as pd
pd.set_option('display.max_rows', None)

directory_path = './logs/dut3/logs_client'
file_pattern = 'Client_dut*'

# Use glob to find all files matching the pattern
file_paths = glob.glob(os.path.join(directory_path, file_pattern))

In [2]:
with open('crcTable.txt', 'r') as file:
    crcTable = [int(line.strip(), 16) for line in file]

In [3]:
frames = []
frame_parsing_errors = 0
crc_errors = 0
filtered_frames = []
for file_path in file_paths:
    with open(file_path, 'r') as file:
        for json_line in file:
            # Parse frame
            try:
                frame = json.loads(json_line)
            except Exception as error:
                print(f"Failed decoding JSON for file {file_path}: {error}")
            frames.append(frame)

# Sort frames based on timestamp
sorted_frames = sorted(frames, key=lambda x: x["timestamp"])
parsed_frames = []

In [4]:
def check_crc(payload, payload_length, crc_value):
        INITIAL_REMAINDER = 0xFFFF
        FINAL_XOR_VALUE = 0x0000
        remainder = INITIAL_REMAINDER

        for byte in range(payload_length):
            data = payload[byte] ^ (remainder >> (16 - 8))
            remainder = crcTable[data] ^ (remainder << 8) & 0xFFFF

        return crc_value == (remainder ^ FINAL_XOR_VALUE)

In [5]:
import struct

# +--------+--------------------+-------------+---------------+
# | Format | C Type             | Python type | Standard size |
# +--------+--------------------+-------------+---------------+
# | x      | pad byte           | no value    | (7)           |
# | c      | char               | bytes       | 1             |
# | b      | signed char        | integer     | 1             |
# | B      | unsigned char      | integer     | 1             |
# | ?      | _Bool              | bool        | 1             |
# | h      | short              | integer     | 2             |
# | H      | unsigned short     | integer     | 2             |
# | i      | int                | integer     | 4             |
# | I      | unsigned int       | integer     | 4             |
# | l      | long               | integer     | 4             |
# | L      | unsigned long      | integer     | 4             |
# | q      | long long          | integer     | 8             |
# | Q      | unsigned long long | integer     | 8             |
# | n      | ssize_t            | integer     | (3)           |
# | N      | size_t             | integer     | (3)           |
# | e      | (6)                | float       | 2             |
# | f      | float              | float       | 4             |
# | d      | double             | float       | 8             |
# | s      | char[]             | bytes       | (9)           |
# | p      | char[]             | bytes       | (8)           |
# | P      | void*              | integer     | (5)           |
# +--------+--------------------+-------------+---------------+


frame_id_formatting = {
    "BBBBBBBBBBBBBBBBBBBBBBBBBBBBBBBB": 0,  # test frame
    # "II": 1,  # fini
    "IIIII": 1,  # fini
    "IIIIII": 16,  # exception
}


def parse_payload(data, frame_id):
    # Ensure that the data is a bytes object
    # if not isinstance(data, bytes):
    #     raise ValueError("Data must be bytes")

    # Find the format string for the given frame_id
    format_str = None
    unpacked_data = ()
    for fmt_str, id in frame_id_formatting.items():
        if id == frame_id:
            format_str = fmt_str
            break

    if format_str is None:
        raise ValueError(f"No format string found for frame ID {frame_id}")

    # Unpack the data dynamically based on the format string
    try:
        unpacked_data = struct.unpack(format_str, data)
    except struct.error as e:
        print(f"Error unpacking data with format {format_str}: {e}, data {data}")

    # # Convert bytes to string for field4 if necessary
    # field4 = field4.decode("utf-8").rstrip("\x00")

    # for field in unpacked_data:
    #     print(hex(field))

    return unpacked_data


In [6]:
def decode_frame(frame_bytes):
    # Desconstructing the frame
    header = frame_bytes[0]
    frame_id = frame_bytes[1]
    payload_length = frame_bytes[2]
    payload = frame_bytes[3 : 3 + payload_length]
    crc_bytes = frame_bytes[3 + payload_length : 5 + payload_length]
    tail = frame_bytes[-1]

    # Concatenating the CRC bytes into a single number
    # Assuming CRC is in big-endian format
    crc = (crc_bytes[0] << 8) | crc_bytes[1]

    # Converting payload to hex representation
    payload_hex = [hex(byte) for byte in payload]

    crc_check = check_crc(payload, payload_length, crc)

    data = None

    if crc_check is False:
        print(f"CRC Check failed!")
    else:
        data = parse_payload(payload, frame_id)

    return data

In [7]:
for frame in sorted_frames:
    frame['timestamp'] = str(datetime.utcfromtimestamp(float(frame['timestamp'])).replace(tzinfo=timezone.utc).strftime('%Y-%m-%d %H:%M:%S.%f UTC'))
    if 'data' in frame:
        try:
            decoded_frame = decode_frame(bytes.fromhex(frame['data']))
            #CRC check failed
            if decoded_frame == None:
                parsed_frames.append({'timestamp': frame['timestamp'], 'error': "CRC check error"})
                crc_errors += 1
            # Exception
            elif len(decoded_frame) < 5:
                parsed_frames.append({'timestamp': frame['timestamp'], 'error': f"Frame parsing error. Data field too small: {decode_frame}"})
            # Data correct
            else:
                frame['data'] = decoded_frame
                parsed_frames.append(frame)
        except Exception as error:
            frame_parsing_errors += 1
            parsed_frames.append({'timestamp': frame['timestamp'], 'error': "Frame parsing error (possibly due to comm failure)"})
            #print(f"Parsing error! {error}")
    elif 'event' in frame:
        parsed_frames.append(frame)

CRC Check failed!
CRC Check failed!
CRC Check failed!
CRC Check failed!
CRC Check failed!
CRC Check failed!
CRC Check failed!


In [8]:
previous_entry = None
# Filtering duplicate payloads out
for frame in parsed_frames:
    if previous_entry is None or frame['data'] != previous_entry or 'error' in frame:
        #frame['payload'] = frame.pop('data')
        filtered_frames.append(frame)

In [9]:
data_frame = []

for frame in parsed_frames:
    print(frame)
    if 'data' in frame:
        parsed_payload = (frame['timestamp'],) + frame['data']
        keys = ['timestamp', 'total_errors', 'count1', 'count2', 'count3', 'count4']
        mapping = {num: key for num, key in zip(keys, parsed_payload)}
        data_frame.append(mapping)

df = pd.DataFrame(data_frame)
df

{'message': '', 'type': 'Serial dut3_monitor', 'id': 20, 'timestamp': '2023-12-09 15:15:09.881740 UTC', 'data': (3, 45325736, 11245361, 10521517, 229083)}
{'message': '', 'type': 'Serial dut3_monitor', 'id': 20, 'timestamp': '2023-12-09 15:15:30.566581 UTC', 'data': (3, 45307857, 11245361, 10521517, 228621)}
{'message': '', 'type': 'Serial dut3_monitor', 'id': 19, 'timestamp': '2023-12-09 15:15:30.569447 UTC', 'event': 'Serial Timeout'}
{'message': '', 'type': 'Serial dut3_monitor', 'id': 20, 'timestamp': '2023-12-09 15:15:33.416330 UTC', 'data': (3, 45305841, 11245361, 10521517, 229099)}
{'message': '', 'type': 'Serial dut3_monitor', 'id': 20, 'timestamp': '2023-12-09 15:15:36.247993 UTC', 'data': (3, 45322195, 11245361, 10521517, 229029)}
{'message': '', 'type': 'Serial dut3_monitor', 'id': 20, 'timestamp': '2023-12-09 15:15:39.063543 UTC', 'data': (3, 45307378, 11245361, 10521517, 228782)}
{'message': '', 'type': 'Serial dut3_monitor', 'id': 20, 'timestamp': '2023-12-09 15:15:41.895

timestamp  total_errors     count1    count2  \
0      2023-12-09 15:15:09.881740 UTC             3   45325736  11245361   
1      2023-12-09 15:15:30.566581 UTC             3   45307857  11245361   
2      2023-12-09 15:15:33.416330 UTC             3   45305841  11245361   
3      2023-12-09 15:15:36.247993 UTC             3   45322195  11245361   
4      2023-12-09 15:15:39.063543 UTC             3   45307378  11245361   
5      2023-12-09 15:15:41.895676 UTC             3   45316030  11245361   
6      2023-12-09 15:15:44.726848 UTC             3   45327247  11245361   
7      2023-12-09 15:15:47.542019 UTC             3   45322460  11245361   
8      2023-12-09 15:15:50.373580 UTC             3   45318780  11245361   
9      2023-12-09 15:15:53.204805 UTC             3   45311272  11245361   
10     2023-12-09 15:15:56.021030 UTC             3   45324441  11245361   
11     2023-12-09 15:15:58.851337 UTC             3   45321434  11245361   
12     2023-12-09 15:16:01.683396 UTC             3   45304069  11245361   
13     2023-12-09 15:16:04.499318 UTC             3   45314855  11245361   
14     2023-12-09 15:16:07.330925 UTC             3   45317741  11245361   
15     2023-12-09 15:16:10.162788 UTC             3   45320255  11245361   
16     2023-12-09 15:16:12.977655 UTC             3   45304152  11245361   
17     2023-12-09 15:16:15.713329 UTC             3   43896439  10497699   
18     2023-12-09 15:16:18.384475 UTC             3   42595662   9820490   
19     2023-12-09 15:16:21.040153 UTC             3   42607400   9820490   
20     2023-12-09 15:16:23.695554 UTC             3   42604790   9820490   
21     2023-12-09 15:16:26.351784 UTC             3   42606116   9820490   
22     2023-12-09 15:16:29.006499 UTC             3   42633882   9820490   
23     2023-12-09 15:18:44.580908 UTC             0   45307729  11242375   
24     2023-12-09 15:18:47.396324 UTC             0   45305080  11242375   
25     2023-12-09 15:21:18.659514 UTC             0   45307141  11242375   
26     2023-12-09 15:25:13.626615 UTC             0   45312156  11242375   
27     2023-12-09 15:25:16.457435 UTC             0   45319746  11242375   
28     2023-12-09 15:25:36.223559 UTC             0   45314975  11242375   
29     2023-12-09 15:25:39.055035 UTC             0   45324673  11242375   
30     2023-12-09 15:25:51.614001 UTC             0   45309057  11242375   
31     2023-12-09 15:25:54.445750 UTC             0   45323426  11242375   
32     2023-12-09 15:26:14.273054 UTC             0   45304782  11242375   
33     2023-12-09 15:26:17.104502 UTC             0   45314136  11242375   
34     2023-12-09 15:26:19.935954 UTC             0   45307097  11242375   
35     2023-12-09 15:26:22.750899 UTC             0   45320356  11242375   
36     2023-12-09 15:26:25.583107 UTC             0   45301149  11242375   
37     2023-12-09 15:32:52.224851 UTC             0   45306938  11242375   
38     2023-12-09 15:32:55.054939 UTC             0   45324559  11242375   
39     2023-12-09 15:32:57.886864 UTC             0   45324195  11242375   
40     2023-12-09 15:33:00.702429 UTC             0   45314808  11242375   
41     2023-12-09 15:33:03.534098 UTC             0   45302539  11242375   
42     2023-12-09 15:33:06.365497 UTC             0   45332213  11242375   
43     2023-12-09 15:33:09.181685 UTC             0   45302944  11242375   
44     2023-12-09 15:33:12.011934 UTC             0   45304720  11242375   
45     2023-12-09 15:33:14.843849 UTC             0   45303363  11242375   
46     2023-12-09 15:33:17.659859 UTC             0   45307388  11242375   
47     2023-12-09 15:35:39.237884 UTC             0   45311487  11242375   
48     2023-12-09 15:35:42.068276 UTC             0   45306219  11242375   
49     2023-12-09 15:35:44.884250 UTC             0   45323635  11242375   
50     2023-12-09 15:35:47.714926 UTC             0   45324936  11242375   
51     2023-12-09 15:35:50.546620 UTC             0   45315594  11242375   
